In [3]:
%%capture

!pip install git+https://github.com/huggingface/datasets.git
!pip install git+https://github.com/huggingface/transformers.git
!pip install hazm

In [5]:
from hazm import word_tokenize
from hazm import sent_tokenize
import re
import six

# from normalizer import normalize

persian_regex = "0-9۰۱۲۳۴۵۶۷۸۹ءآئابتثجحخدذرزسشصضطظعغفقلمنهوپچژکگیە\u200c"


def filter_by_lang_regex(text, ratio=0.7, regex="0-9۰۱۲۳۴۵۶۷۸۹ءآئابتثجحخدذرزسشصضطظعغفقلمنهوپچژکگیە\u200c"):
    candidate_text = re.sub(r"[^" + regex + "]+", " ", six.ensure_str(text)).replace(" ", "")
    text = text.replace(" ", "")

    return True if (len(candidate_text) / len(text)) > ratio else False


def filter_by_num_tokens(text, gt=64):
    return True if len(word_tokenize(text)) > gt else False


def filter_by_num_sents(text, gt=2):
    return True if len(sent_tokenize(text)) > gt else False


def normalizer(text, do_lowercase=False):
    if do_lowercase:
        text = text.lower()

    return text


In [7]:
import ast
import logging
import os
import sys
from dataclasses import dataclass, field
from typing import Dict, List, Optional, Tuple

from datasets import load_dataset
from tokenizers import ByteLevelBPETokenizer
from transformers import (
    HfArgumentParser,
)

# from data_utils import (
#     filter_by_lang_regex,
#     filter_by_num_tokens,
#     filter_by_num_sents,
#     normalizer
# )

In [11]:
raw_dataset = load_dataset(
    "oscar",
    "unshuffled_deduplicated_fa",
    split="train[:1%]"
)

raw_dataset

Dataset oscar downloaded and prepared to /root/.cache/huggingface/datasets/oscar/unshuffled_deduplicated_fa/1.0.0/84838bd49d2295f62008383b05620571535451d84545037bb94d6f3501651df2. Subsequent calls will reuse this data.


Dataset({
    features: ['id', 'text'],
    num_rows: 820350
})

In [12]:
raw_dataset

Dataset({
    features: ['id', 'text'],
    num_rows: 820350
})

In [13]:
dataset = raw_dataset.filter(lambda example: filter_by_lang_regex(example["text"], ratio=0.75))
dataset = dataset.filter(lambda example: filter_by_num_tokens(example["text"], gt=128))
dataset = dataset.filter(lambda example: filter_by_num_sents(example["text"], gt=2))
dataset = dataset.map(normalizer)

In [14]:
dataset

Dataset({
    features: ['id', 'text'],
    num_rows: 473687
})

In [18]:
dataset[1]["text"]

'قـــــــــــــــــرار بود با هم کنـــــــــــــار بیایم نه اینکه از کنــــــــــــار هم رد بشیم...!!!\nاگر روزی دلت لبریز غم بود گذارت بر مزار کهنه ام بود بگو این بی نصیب خفته در خاک یه روزی عاشق و دیوانه ام بود...\nخبر به دورترین نقطه جهان برسد نخواست او به من خسته ، بی کمان برسد شکنجه بیشتر از این که پیش چشم خودت کسی که سهم تو باشد به دیگران برسد خدا کند ، که نفرین نمی کنم نکند به او که عاشق او بوده ام زیان برسد خدا کند فقط این عشق از سرم برود خدا کند که فقط زود آن زمان برسد...\nترسم که شبی از غم ناگه بمیرم در بستر دلسوز با آه بمیرم آن لحظه آخر که اجل گفت بمیر ای کاش تو را بینم و آنگاه بمیرم\nخوشبختی را دیروز به حراج گذاشتند ولی حیف که من زاده ی امروزم... خدایا جهنم فرداست پس چرا امروز می سوزم ؟!!\nدر کرانه محبت رنگ چشمانت را دیدم در عمق بی کران آسمان رخ تو را دیدم دیدنت آرزوی من شده آن را از من دریغ مکن\nکوه باشی صخره هایت می شوم... اشک باشی دیدگانت می شوم... رود باشی چشمه سارت می شوم... دوست باشی دوستدارت می شوم...!'

In [19]:
dataset[1]["text"]

'قـــــــــــــــــرار بود با هم کنـــــــــــــار بیایم نه اینکه از کنــــــــــــار هم رد بشیم...!!!\nاگر روزی دلت لبریز غم بود گذارت بر مزار کهنه ام بود بگو این بی نصیب خفته در خاک یه روزی عاشق و دیوانه ام بود...\nخبر به دورترین نقطه جهان برسد نخواست او به من خسته ، بی کمان برسد شکنجه بیشتر از این که پیش چشم خودت کسی که سهم تو باشد به دیگران برسد خدا کند ، که نفرین نمی کنم نکند به او که عاشق او بوده ام زیان برسد خدا کند فقط این عشق از سرم برود خدا کند که فقط زود آن زمان برسد...\nترسم که شبی از غم ناگه بمیرم در بستر دلسوز با آه بمیرم آن لحظه آخر که اجل گفت بمیر ای کاش تو را بینم و آنگاه بمیرم\nخوشبختی را دیروز به حراج گذاشتند ولی حیف که من زاده ی امروزم... خدایا جهنم فرداست پس چرا امروز می سوزم ؟!!\nدر کرانه محبت رنگ چشمانت را دیدم در عمق بی کران آسمان رخ تو را دیدم دیدنت آرزوی من شده آن را از من دریغ مکن\nکوه باشی صخره هایت می شوم... اشک باشی دیدگانت می شوم... رود باشی چشمه سارت می شوم... دوست باشی دوستدارت می شوم...!'

In [17]:
dataset[2]["text"]

'«یكی از كهن ترین و سنتی ترین روش های انسان برای انتقال معرفت به نسل های بعد، قصه ها و حكایات بوده است. قصه، ناب ترین و خالص ترین بخش ادبیات است؛ چرا كه ما را به دورانی پیش از پیدایش تفاسیر و تعابیر امروز مان می برد. قصه ها شادند، سرگرم كننده اند، نمایشی اند، اما فراتر از همه ، معرفت را به شكلی دلپذیر منتقل می كنند.»\nیک بام و دو هوا خودکشی کن!!/طنز خران آزاد و... خوبی خوبی است! نگرانی از اتهام ناحق! آدمایی از جنس بلور چه حاجتی به قهرمان؟! و عدالت اجرا شد!! پرنده ات را آزاد کن! برخورد پیامبر با زنِ خواننده من مسئول کره ها هستم!!! شایعه مرگ شاه! بالا نرو، بسیار خطرناک است!! .... همچنان در منزل اول اسیر! "کلام امید" لیست آخرین پستها\nحكایت و داستان پرتال فرهنگی مذهبی لاهوت مشاوره و روانشناسی(مهدی معتقد) آنتی صهیونیسم نخود به اندیشان پیام امیر(ع) پیام های پیامبر(ص) وب نامه مدارا حکایات حکیمانه آیا به از این نمی توان بود؟ وب باران شفیعی مطهر همه پیوندها\nقصه های شهرهرت(11) سخنان كوتاه حكیمانه(210) سروده های حكیمانه(165) طنزهای حكیمانه(394) حكایات حكیمانه(806)'

In [20]:
dataset[3]["text"]

'حرکت اصلاح طلبی به معنای یک جریان رفورمیستی، در داخل حاکمیت کنونی، محصول یک پروسۀ کشمکش طولانی درون حکومتی است که ریشه های آن به سالهای بعد از پایان جنگ ایران و عراق و حوادث قبل از 2 خرداد 1376 برمیگردد. این جریان آميزه ای از نيروهای اصلاح طلب مذهبی و سرخورده از انحصار طلبی های جناح تندرو و محافظه کار و بخشی از مردم معترض برخاسته از طبقۀ متوسط جدیداست که به شعارهای رهبران این طیف باور داشته و در رکاب آن قدم برمی دارند. اصلاح طلبان درون حکومتی می کوشند نشان دهند که آنان نه تنها خواهان يک حکومت دموکراتيک و پای بند به اصول مدرن و دموکراتیک و اعلاميۀ جهانی حقوق بشر هستند بلکه درصدد اثبات این مقوله نیز می باشند که تحقق دموکراسی در شکل اسلامی آن ممکن و امکانپذیر است. این حرکت با پذیرفتن چهارچوب نظام جمهوری اسلامی و وفاداری به قانون اساسی آن در پی اصلاحاتی در درون نظام و در پی قبضۀ دوبارۀ قدرت سیاسی است.\nاما در کنار این حرکت رفرمیستی جنبش آزادیخواهانه ای بس گسترده تر و ریشه دارتری در جامعۀ ایران در جریان است که ریشه های تاریخی آن به انقلاب مشروطیت و پروسۀ قبل از کودتای 1299 و روی کار آورده 

In [21]:
dataset[10]["text"]

'آینه نیوز: قطعه موسیقی «ای دریغا» در آستانه توزیع اولین قسمت از فصل دوم سریال «شهرزاد» منتشر شد. این اثر که با صدای محسن چاوشی و همراهی آواز سینا سرلک، دوست و همراه قدیمی چاوشی همراه است، «ای دریغا» نام دارد که حسین صفا آن را سروده و محسن چاوشی آهنگسازی کرده و شهاب اکبری تنظیم آن را به عهده داشته است. در «ای دریغا»، احسان نی زن به عنوان نوازنده کمانچه و مجتبی تقی پور به عنوان نوازنده گیتار همکاری داشته اند.\nدر فصل اول سریال شهرزاد تولید و پخش قطعات متعدد موسیقی در کنار توزیع سریال مورد توجه مخاطبان قرا گرفته بود و حالا در فصل دوم نیز همین رویه توسط عوامل تولید «شهرزاد» مورد نظر قرار گرفته است.'

In [22]:
dataset[20]["text"]

'امتیاز شما به این کانالوبسایت پردیس ایرانیان آموزش دوره های تخصصی ماساژ زیر نظر مربی فنی و حرفه ای عنوان سایت : پردیس ایرانیان لینک سایت : http://pardisiranian.ir/ آی دی اینستاگرام : pardisiranian.info@ لینک اینستاگرام: […]\nLeave a commentپیج اینستاگرام, کانال برنزی, لینک سایتآموزش ماساژ زیر نظر فنی حرفه ای, آموزش ماساژ فنی حرفه ای, آموزش ماساژ فنی حرفه ای تهران, دوره ماساژ فدراسیون پزشکی ورزشی, فدراسیون بین المللی ماساژ ایران, ماساژ آروماتراپی, ماساژ تخصصی, ماساژ سوئدی, ماساژ لیفتینگ صورت, مربی آموزش ماساژ\t\nبایگانی کانالها گزینش ماه اکتبر 2018 سپتامبر 2018 آگوست 2018 جولای 2018 ژوئن 2018 می 2018 آوریل 2018 فوریه 2018\nکانال ها بر اساس موضوع گزینش دسته پیج اینستاگرام ربات پیام رسان بله سایر کانال ها کانال آموزشی کانال آی گپ کانال اجتماعی-سیاسی-فرهنگی کانال ایتا کانال برنزی کانال بله کانال بیسفون کانال تجاری کانال تفریحی کانال تلگرام کانال خبری کانال رسمی کانال سروش کانال سلام کانال شخصی کانال گپ کانال محلی کانال نقره ای کانال های طلایی کانال ویسپی لینک سایت مطالب سایت\nکانال تبلیغا

In [23]:
dataset[30]["text"]

'سیستم پرده برقی شاید در نگاه اول عنصر پرکاربردی درخانه هوشمند به نظر نرسد. اما با کمی تامل در می یابیم که با کمک این سیستم میتوان براحتی انواع مدل های پرده برقی، کرکره و سایبان را با روش های مختلف کنترل نماییم. به کمک این سیستم می توانید با استفاده ازکلیدهای هوشمند، یا از روی صفحه نمایش لمسی منزلتان و یا به وسیله ی اپلیکیشن نصب شده بر روی گوشی و تبلت خود در سناریو های متفاوت، از راه دور میزان نور وارد شده به منزلتان را تنظیم نموده و آنها را کنترل نمایید. در سیستم هوشمند، پرده برقی می تواند در صورت نیاز کاربر، بصورت اتوماتیک در زمان های مختلف و یا تحت عواملی همچون تمایز شدت نور داخل و خارج ساختمان و یا شدت گرمای محیط باز و بسته شوند بدون آنکه نیاز به صرف وقت و انرژی خاصی جهت مدیریت وضعیت پرده ها باشد.\nطیف گسترده ای از انواع پرده های موجود در بازار قابلیت اجرا در سیستم هوشمند را دارند. از جمله، پرده های رول، پرده های از کنار جمع شو، پرده های بالارو با امکان ایجاد سایه روشن. تنها تفاوت در نوع موتورهای برقی به کار رفته در این سیستم می باشد. برای مثال در پرده های رولی به موتوری احتیاج دار

In [24]:
dataset[200]["text"]

'کمیسیون مستقل انتخابات افغانستان می گوید که نتیجه ابتدایی دور دوم انتخابات ریاست جمهوری این کشور چهارشنبه یازدهم سرطان/تیر اعلام خواهد شد.\nنور محمد نور سخنگوی این کمیسیون به بی\u200cبی\u200cسی گفت که کمیسیون مستقل انتخابات آمادگی های لازم برای اعلام نتیجه انتخابات را دارد و بر اساس جدول زمانی تعیین شده پیش خواهد رفت.\nساعاتی پس از درگذشت محمد قسیم فهیم معاون اول رئیس جمهوری افغانستان (جانشین احمدشاه مسعود رهبر پیشین جبهه مقاوت علیه طالبان) بحث\u200cها در مورد تاثیر نبود آقای فهیم در انتخابات ریاست جمهوری افغانستان بالا گرفته\u200cاست. تا برگزاری انتخابات ریاست جمهوری ۱۳۹۳ افغانستان کمتر از یک ماه باقی مانده\u200cاست. آقای فهیم در این انتخابات صراحتا اعلام نکرده بود که از کدام نامزد حمایت می\u200cکند اما ستاد انتخاباتی عبدالله عبدالله بیشتر از یکبار اعلام کرد که مارشال فهیم در این انتخابات از آقای عبدالله حمایت می\u200cکند.\nآقای فهیم و سخنگویانش هیچگاهی این ادعای ستاد انتخاباتی داکتر عبدالله را تایید یا رد نکردند. محی\u200cالدین مهدی، عضو مجلس نمایندگان افغانستان و از اعضای پیشین حزب

In [25]:
dataset[2000]["text"]

'مناقصه با عنوان واگذاری کف پوش معابر و با کد هزاره 795072 در تاریخ پنجشنبه، 8 مرداد 1394 در سایت ارتباط گستران هزاره منتشر شده و مهلت شرکت در آن تا تاریخ 1394/05/19 می باشد. این آگهی مربوط به استان تهران بوده و در دسته بندی (های) سایر مناقصه های راهسازی، سایر مناقصه های ساختمان انتشار یافته است.\nمبلغ سپرده به میزان 100.000.000 ریال - جهت دریافت اسناد با ارائه معرفی نامه معتبر و تصویر رتبه بندی معتبر - جهت دریافت اسناد معرفی نامه معتبر(بهمراه کارت شناسایی ملی) و اصل فیش واریزی بمبلغ 200.000 ریال به حساب شماره 100790829443 بانک شهر بنام شهرداری ملارد- هزینه آگهی به عهده برنده می باشد\nکلمات کلیدی: مناقصه های استان تهران , مناقصه های سایر مناقصه های راهسازی , مناقصه های سایر مناقصه های ساختمان , مناقصه های شهرداری ملارد , مناقصات , مزایده ها , استعلام ها , استعلام های آنلاین , سایت مناقصات , اسناد مناقصه\nارتباط گستران هزاره اولین مرکز تخصصی جمع آوری و اطلاع رسانی آگهی های تجاری مناقصه، مزایده و استعلام بها در کشور دارای گواهی رتبه بندی و احراز صلاحیت از شورای عالی انفورماتیک کشور و مجو

In [26]:
dataset[500]["text"]

'برای خرید فقط و فقط از سایت اصلی شرکت اقدام فرمایید. شرکت جیشیر جز در سایت رسمی که تبلیغاتش را در سایت میبینید ، هیچ سایت دیگری ندارد\nدر صورتی که برای اولین بار از این سایت بازدید می کنید, لازم است تا راهنمای سایت را مطالعه فرمایید . در صورتی که هنوز عضو نشده اید برای ارسال مطالب , دانلود فایل ها, دسترسی به انجمن های ویژه کاربران و ...عضو شده و در سایت ثبت نام کنید . با کلیک بر روی ثبت نام در مدت کوتاهی عضو سایت شده و از مطالب و امکانات سایت بهره مند شوید .\nسایت ماهواره مای کسری سایت پلاست سایت ماهواره پلاست انجمن جیشیر بازکردن کانالهای قفل شده بازکردن کانالهای کارتی ماهواره خريد شيرينگ هوايي تمدید اکانت هوایی و اینترنتی خرید شیرینگ هوایی و اینترنتی گلوبال خرید اکانت هوایی ماهواره فروش اکانت جیشیر خرید اکانت جیشیر خرید اکانت gshare تمدید اکانت جیشیر فروش اکانت gshare خرید شیرینگ هوایی و اینترنتی ای ستار istar خرید شیرینگ هوایی و اینترنتی رسیور فروش شیرینگ اسکار ومدیااستار تمدید شیرینگ هوایی و اینترنتی تمدید اکانت شیرینگ هوایی و اینترنتی اسکار خریدد شیرینگ رسیور وماهواره تمدید شیرینگ